In [1]:
# Load libraries

import osmnx as ox
import geopandas as gpd
import pandas as pd
import numpy as np
from pathlib import Path

import folium
from folium.plugins import MarkerCluster

In [2]:
# Load POI dataset
unified_gdf = gpd.read_file("data/unified_pois_brooklyn.geojson")
buildings_4326 = gpd.read_file("data/buildings_brooklyn.geojson")

In [4]:
# Inspect Results: ~1000 Buildings with POIs

# Focus on a specific neighborhood for detailed inspection
# Using Park Slope / Prospect Heights area as example (good mix of uses)

# Define bounding box for inspection area
# Park Slope / Prospect Heights: ~1000 buildings

INSPECT_BOUNDS = {
    'min_lat': 40.670,
    'max_lat': 40.680,
    'min_lon': -73.980,
    'max_lon': -73.965
}

# Filter buildings in the inspection area
inspect_buildings = buildings_4326[
    (buildings_4326.geometry.centroid.y >= INSPECT_BOUNDS['min_lat']) &
    (buildings_4326.geometry.centroid.y <= INSPECT_BOUNDS['max_lat']) &
    (buildings_4326.geometry.centroid.x >= INSPECT_BOUNDS['min_lon']) &
    (buildings_4326.geometry.centroid.x <= INSPECT_BOUNDS['max_lon'])
].copy()

print(f"Buildings in inspection area: {len(inspect_buildings):,}")

# Get POIs for these buildings
inspect_building_ids = set(inspect_buildings['building_id'].values)
inspect_pois = unified_gdf[unified_gdf['building_id'].isin(inspect_building_ids)].copy()

print(f"POIs in inspection area: {len(inspect_pois):,}")
print(f"\nPOI breakdown in inspection area:")
print(inspect_pois['poi_type'].value_counts().head(15))

# Color map for building fill based on primary POI type
poi_fill_colors = {
    'residential': '#3388ff',      # Blue
    'restaurant': "#ff8c00",       # Dark orange
    'cafe': '#ffa500',             # Orange
    'bar': '#800080',              # Purple
    'fast_food': '#ff6347',        # Tomato
    'supermarket': '#228b22',      # Forest green
    'convenience': '#32cd32',      # Lime green
    'clothes': '#90ee90',          # Light green
    'office': '#808080',           # Gray
    'commercial': '#a9a9a9',       # Dark gray
    'school': '#dc143c',           # Crimson
    'hospital': '#ff0000',         # Red
    'clinic': '#ff6b6b',           # Light red
    'place_of_worship': '#8b0000', # Dark red
    'bank': '#4682b4',             # Steel blue
    'hotel': '#daa520',            # Goldenrod
    'industrial': '#2f4f4f',       # Dark slate gray
    'warehouse': '#696969',        # Dim gray
    'fitness_centre': '#ff69b4',   # Hot pink
    'pharmacy': '#00ced1',         # Dark turquoise
}

def get_fill_color(poi_type):
    return poi_fill_colors.get(poi_type, '#3388ff')  # Default blue

# Create map centered on inspection area
center_lat = (INSPECT_BOUNDS['min_lat'] + INSPECT_BOUNDS['max_lat']) / 2
center_lon = (INSPECT_BOUNDS['min_lon'] + INSPECT_BOUNDS['max_lon']) / 2
m = folium.Map(location=[center_lat, center_lon], zoom_start=16, tiles="CartoDB positron")

# Get primary POI type for each building (by sqft)
building_primary_poi = inspect_pois.groupby('building_id').apply(
    lambda x: x.loc[x['sqft'].idxmax(), 'poi_type'] if len(x) > 0 else 'residential'
).to_dict()

# Add building polygons
for idx, bldg in inspect_buildings.iterrows():
    bldg_id = bldg['building_id']
    primary_poi = building_primary_poi.get(bldg_id, 'residential')
    
    # Get all POIs for this building
    bldg_pois = inspect_pois[inspect_pois['building_id'] == bldg_id]
    
    # Build popup content
    popup_html = f"""
    <b>Building ID:</b> {bldg_id}<br>
    <b>Total SqFt:</b> {bldg['total_sqft']:,.0f}<br>
    <b>Floors:</b> {bldg['estimated_floors']}<br>
    <b>Footprint:</b> {bldg['footprint_sqft']:,.0f} sqft<br>
    <hr>
    <b>POIs ({len(bldg_pois)}):</b><br>
    """
    for _, poi in bldg_pois.iterrows():
        popup_html += f"• {poi['poi_type']}: {poi['sqft']:,.0f} sqft ({poi['source']})<br>"
    
    # Add building polygon
    folium.GeoJson(
        bldg.geometry.__geo_interface__,
        style_function=lambda x, color=get_fill_color(primary_poi): {
            'fillColor': color,
            'color': 'black',
            'weight': 1,
            'fillOpacity': 0.6
        },
        popup=folium.Popup(popup_html, max_width=300)
    ).add_to(m)

# Add POI markers on top
for idx, poi in inspect_pois.iterrows():
    if poi['source'] == 'osm_poi':  # Only show actual OSM POIs as markers
        folium.CircleMarker(
            location=[poi.geometry.y, poi.geometry.x],
            radius=4,
            color='white',
            weight=2,
            fill=True,
            fillColor=get_fill_color(poi['poi_type']),
            fillOpacity=1,
            popup=f"<b>{poi['name'] or 'Unnamed'}</b><br>Type: {poi['poi_type']}<br>SqFt: {poi['sqft']:,.0f}"
        ).add_to(m)

# Add legend
legend_html = '''
<div style="position: fixed; bottom: 50px; left: 50px; z-index: 1000; 
            background-color: white; padding: 10px; border: 2px solid gray; 
            border-radius: 5px; font-size: 11px; max-height: 300px; overflow-y: auto;">
<b>Building Primary Use</b><br>
<i style="background:#3388ff;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Residential<br>
<i style="background:#ff8c00;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Restaurant<br>
<i style="background:#ffa500;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Cafe<br>
<i style="background:#228b22;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Supermarket<br>
<i style="background:#32cd32;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Convenience<br>
<i style="background:#808080;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Office<br>
<i style="background:#dc143c;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> School<br>
<i style="background:#8b0000;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Place of Worship<br>
<i style="background:#2f4f4f;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Industrial<br>
<hr>
<b>○</b> = OSM POI marker<br>
Click buildings for details
</div>
'''
m.get_root().html.add_child(folium.Element(legend_html))

# Add bounding box outline
folium.Rectangle(
    bounds=[
        [INSPECT_BOUNDS['min_lat'], INSPECT_BOUNDS['min_lon']],
        [INSPECT_BOUNDS['max_lat'], INSPECT_BOUNDS['max_lon']]
    ],
    color='red',
    weight=2,
    fill=False,
    dash_array='5, 5'
).add_to(m)

print(f"\n=== Inspection Map ===")
print(f"Area: Park Slope / Prospect Heights")
print(f"Buildings shown: {len(inspect_buildings):,}")
print(f"POIs shown: {len(inspect_pois):,}")
print("Click on any building to see POI details")
m

/var/folders/0q/g6bf_xks01543mczt656f8nc0000gn/T/ipykernel_74113/315939835.py:18: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  (buildings_4326.geometry.centroid.y >= INSPECT_BOUNDS['min_lat']) &
/var/folders/0q/g6bf_xks01543mczt656f8nc0000gn/T/ipykernel_74113/315939835.py:19: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  (buildings_4326.geometry.centroid.y <= INSPECT_BOUNDS['max_lat']) &
/var/folders/0q/g6bf_xks01543mczt656f8nc0000gn/T/ipykernel_74113/315939835.py:20: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  (buildings_4326.geometry.centroid.x >= INSPECT_BOUNDS['mi

Buildings in inspection area: 3,226
POIs in inspection area: 3,638

POI breakdown in inspection area:
poi_type
residential         3122
restaurant            56
unknown               48
fast_food             34
cafe                  27
beauty                21
hairdresser           18
estate_agent          18
dentist               18
place_of_worship      17
convenience           16
school                13
kindergarten          11
office                10
fitness_centre        10
Name: count, dtype: int64


/var/folders/0q/g6bf_xks01543mczt656f8nc0000gn/T/ipykernel_74113/315939835.py:67: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  building_primary_poi = inspect_pois.groupby('building_id').apply(



=== Inspection Map ===
Area: Park Slope / Prospect Heights
Buildings shown: 3,226
POIs shown: 3,638
Click on any building to see POI details


## Trip Generators Map - Point-based Visualization

This map shows each trip generator as an individual point, allowing inspection of the data attached to each generator including the converted units for trip generation.

In [ ]:
# Load or create trip generators dataset
import sys
from pathlib import Path
sys.path.insert(0, str(Path.cwd() / 'src'))

# Check if trip_generators file exists, otherwise create from unified POIs
trip_gen_file = Path("data/trip_generators_brooklyn.geojson")
if trip_gen_file.exists():
    print("Loading existing trip generators dataset...")
    trip_generators_gdf = gpd.read_file(trip_gen_file)
else:
    print("Creating trip generators from unified POIs...")
    # Import the conversion functions
    from src.trip_generator import convert_to_trip_gen_units, TRIP_GEN_LAND_USE_MAP
    
    # Add trip generation units to unified_gdf
    trip_generators_gdf = unified_gdf.copy()
    
    # Rename columns for clarity
    trip_generators_gdf['land_use_type'] = trip_generators_gdf['poi_type']
    trip_generators_gdf['generator_id'] = trip_generators_gdf['unified_poi_id']
    
    # Convert to trip gen units
    units_data = trip_generators_gdf.apply(
        lambda x: convert_to_trip_gen_units({'land_use_type': x['land_use_type'], 'sqft': x['sqft']}), 
        axis=1
    )
    trip_generators_gdf['trip_gen_value'] = units_data.apply(lambda x: x[0])
    trip_generators_gdf['trip_gen_unit'] = units_data.apply(lambda x: x[1])
    trip_generators_gdf['trip_gen_category'] = units_data.apply(lambda x: x[2])

# Use same inspection bounds
INSPECT_BOUNDS = {
    'min_lat': 40.670,
    'max_lat': 40.680,
    'min_lon': -73.980,
    'max_lon': -73.965
}

# Filter trip generators in the inspection area
inspect_generators = trip_generators_gdf[
    (trip_generators_gdf.geometry.y >= INSPECT_BOUNDS['min_lat']) &
    (trip_generators_gdf.geometry.y <= INSPECT_BOUNDS['max_lat']) &
    (trip_generators_gdf.geometry.x >= INSPECT_BOUNDS['min_lon']) &
    (trip_generators_gdf.geometry.x <= INSPECT_BOUNDS['max_lon'])
].copy()

print(f"Trip generators in inspection area: {len(inspect_generators):,}")
print(f"\nTop 10 trip generation categories in area:")
print(inspect_generators['trip_gen_category'].value_counts().head(10))

# Extended color map for trip generators
generator_colors = {
    'Residential (3 or more floors)': '#3388ff',      # Blue
    'Residential (2 floors or less)': '#6bb6ff',      # Light blue
    'Office (multi-tenant type building)': '#808080',  # Gray
    'Sit Down/High Turnover Restaurant': '#ff8c00',   # Dark orange
    'Fast Food Restaurant without Drive Through Window': '#ff6347',  # Tomato
    'Local Retail': '#32cd32',                        # Lime green
    'Destination Retail': '#90ee90',                  # Light green
    'Supermarket': '#228b22',                         # Forest green
    'Medical Office': '#ff6b6b',                      # Light red
    'Public School (Students)': '#dc143c',            # Crimson
    'Daycare (Children)': '#ff69b4',                  # Hot pink
    'Academic University': '#8b008b',                 # Dark magenta
    'Hotel': '#daa520',                               # Goldenrod
    'Health Club': '#00ced1',                         # Dark turquoise
    'Passive Park Space': '#98fb98',                  # Pale green
    'Active Park Space': '#00fa9a',                   # Medium spring green
    'Museum': '#9370db',                              # Medium purple
    'Cineplex': '#ba55d3',                           # Medium orchid
    'Home Improvement Store': '#cd853f',              # Peru
}

def get_generator_color(category):
    return generator_colors.get(category, '#696969')  # Default dim gray

# Create map centered on inspection area
center_lat = (INSPECT_BOUNDS['min_lat'] + INSPECT_BOUNDS['max_lat']) / 2
center_lon = (INSPECT_BOUNDS['min_lon'] + INSPECT_BOUNDS['max_lon']) / 2
m2 = folium.Map(location=[center_lat, center_lon], zoom_start=16, tiles="CartoDB positron")

# Add trip generator points
for idx, gen in inspect_generators.iterrows():
    # Determine marker size based on value
    if gen['trip_gen_unit'] == 'DU':
        radius = min(8, 3 + gen['trip_gen_value'] * 0.1)  # Size based on dwelling units
    elif gen['trip_gen_unit'] == '1000_sf':
        radius = min(8, 3 + gen['trip_gen_value'] * 0.5)  # Size based on 1000 sq ft
    else:
        radius = 5  # Default size
    
    # Build detailed popup
    popup_html = f"""
    <div style="font-family: monospace; font-size: 12px;">
    <b style="color: {get_generator_color(gen['trip_gen_category'])}">
        {gen.get('name', gen['land_use_type'].title()) or 'Unnamed'}
    </b><br>
    <hr style="margin: 5px 0;">
    <b>Generator ID:</b> {gen.get('generator_id', 'N/A')}<br>
    <b>Building ID:</b> {gen['building_id']}<br>
    <hr style="margin: 5px 0;">
    <b>Land Use:</b> {gen['land_use_type']}<br>
    <b>Source:</b> {gen['source']}<br>
    <hr style="margin: 5px 0;">
    <b>Trip Gen Category:</b><br>
    <span style="color: darkblue;">{gen['trip_gen_category']}</span><br>
    <hr style="margin: 5px 0;">
    <b>Original Size:</b> {gen['sqft']:,.0f} sqft<br>
    <b>Converted:</b> <span style="color: darkgreen; font-weight: bold;">
        {gen['trip_gen_value']:.1f} {gen['trip_gen_unit']}
    </span><br>
    <hr style="margin: 5px 0;">
    <b>Location:</b> {gen.geometry.y:.6f}, {gen.geometry.x:.6f}
    </div>
    """
    
    # Determine opacity based on source
    opacity = 0.8 if gen['source'] == 'osm_poi' else 0.6
    
    folium.CircleMarker(
        location=[gen.geometry.y, gen.geometry.x],
        radius=radius,
        color='white' if gen['source'] == 'osm_poi' else 'gray',
        weight=1,
        fill=True,
        fillColor=get_generator_color(gen['trip_gen_category']),
        fillOpacity=opacity,
        popup=folium.Popup(popup_html, max_width=350),
        tooltip=f"{gen.get('name', '')[:30] or gen['land_use_type']} | {gen['trip_gen_value']:.1f} {gen['trip_gen_unit']}"
    ).add_to(m2)

# Add legend
legend_html2 = '''
<div style="position: fixed; bottom: 50px; left: 50px; z-index: 1000; 
            background-color: white; padding: 10px; border: 2px solid gray; 
            border-radius: 5px; font-size: 11px; max-height: 400px; overflow-y: auto;">
<b>Trip Generator Categories</b><br>
<i style="background:#3388ff;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Residential (3+ floors)<br>
<i style="background:#6bb6ff;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Residential (1-2 floors)<br>
<i style="background:#808080;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Office<br>
<i style="background:#ff8c00;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Restaurant<br>
<i style="background:#ff6347;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Fast Food<br>
<i style="background:#32cd32;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Local Retail<br>
<i style="background:#228b22;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Supermarket<br>
<i style="background:#ff6b6b;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Medical Office<br>
<i style="background:#dc143c;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> School<br>
<i style="background:#daa520;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Hotel<br>
<i style="background:#00ced1;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Health Club<br>
<i style="background:#98fb98;width:12px;height:12px;display:inline-block;border:1px solid black;"></i> Parks<br>
<hr>
<b>Border Colors:</b><br>
⚪ White = OSM POI<br>
⚫ Gray = Inferred<br>
<hr>
<b>Units:</b><br>
DU = Dwelling Units<br>
1000_sf = Per 1,000 sq ft<br>
<hr>
<b>Hover</b> for quick info<br>
<b>Click</b> for full details
</div>
'''
m2.get_root().html.add_child(folium.Element(legend_html2))

# Add bounding box outline
folium.Rectangle(
    bounds=[
        [INSPECT_BOUNDS['min_lat'], INSPECT_BOUNDS['min_lon']],
        [INSPECT_BOUNDS['max_lat'], INSPECT_BOUNDS['max_lon']]
    ],
    color='red',
    weight=2,
    fill=False,
    dash_array='5, 5'
).add_to(m2)

print(f"\n=== Trip Generator Inspection Map ===")
print(f"Area: Park Slope / Prospect Heights")
print(f"Generators shown: {len(inspect_generators):,}")
print("Hover over points for quick info, click for detailed data")
m2

In [ ]:
# Summary statistics for trip generators in inspection area
print("=== Trip Generator Statistics for Inspection Area ===\n")

# Group by unit type
print("Distribution by Unit Type:")
unit_summary = inspect_generators.groupby('trip_gen_unit').agg({
    'generator_id': 'count',
    'trip_gen_value': ['sum', 'mean', 'median']
}).round(1)
unit_summary.columns = ['Count', 'Total_Value', 'Mean_Value', 'Median_Value']
print(unit_summary)

print("\n" + "="*60 + "\n")

# Top categories by total trip generation potential
print("Top 10 Categories by Total Trip Generation Value:")
category_summary = inspect_generators.groupby('trip_gen_category').agg({
    'generator_id': 'count',
    'trip_gen_value': 'sum',
    'trip_gen_unit': 'first'
}).sort_values('trip_gen_value', ascending=False).head(10)
category_summary.columns = ['Count', 'Total_Value', 'Unit']
print(category_summary)

print("\n" + "="*60 + "\n")

# Source breakdown
print("Data Source Distribution:")
source_summary = inspect_generators.groupby('source').agg({
    'generator_id': 'count',
    'sqft': 'sum'
})
source_summary.columns = ['Count', 'Total_SqFt']
source_summary['Avg_SqFt'] = (source_summary['Total_SqFt'] / source_summary['Count']).round(0)
print(source_summary)

print("\n" + "="*60 + "\n")

# Sample trip generators with different units
print("Sample Trip Generators (showing unit conversions):")
samples = inspect_generators.groupby('trip_gen_unit').apply(
    lambda x: x.nlargest(1, 'trip_gen_value'), 
    include_groups=False
)[['land_use_type', 'sqft', 'trip_gen_value', 'trip_gen_unit', 'trip_gen_category']]
samples.columns = ['Land_Use', 'Original_SqFt', 'Converted_Value', 'Unit', 'Trip_Gen_Category']
print(samples.to_string())